In [1]:
import sys
sys.path.insert(0, '../../')
import ccal
%matplotlib inline
%config InlineBackend.figure_formats = {'svg',}

import numpy as np
import pandas as pd

from sklearn.cluster import AgglomerativeClustering
from scipy.cluster.hierarchy import linkage, fcluster, cophenet
from scipy.spatial.distance import pdist
from scipy.spatial import Delaunay, ConvexHull
from sklearn import manifold
from statsmodels.nonparametric.kernel_density import KDEMultivariate
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import seaborn as sns

import numpy as np
import rpy2.robjects as ro
from rpy2.robjects.numpy2ri import numpy2ri
ro.conversion.py2ri = numpy2ri
from rpy2.robjects.packages import importr
mass = importr('MASS')

print_log = ccal.support.print_log
CMAP_CATEGORICAL = ccal.visualize.CMAP_CATEGORICAL

==================== Computational Cancer Analysis Library ====================
<16:47:41> Checking dependencies ...
<16:47:41> Using the following packages:
<16:47:41> 	matplotlib (v1.5.1)
<16:47:41> 	numpy (v1.10.4)
<16:47:41> 	pandas (v0.18.0)
<16:47:41> 	rpy2 (v2.7.9)
<16:47:41> 	scikit-learn (v0.17.1)
<16:47:41> 	scipy (v0.17.0)
<16:47:41> 	seaborn (v0.7.0)


# get_states

In [ ]:
h = ccal.support.read_gct('../../../hematopoietic_cancer/result/ccle_hema/k9/ccle_hema_k_9_H.gct')

ks = list(range(9, 13, 1))

nclustering = 3

labels_filename = '~/Desktop/state_labels.txt'

In [ ]:
# Standardize H and clip values less than -3 and more than 3
standardized_h = ccal.support.standardize_pandas_object(h)
standardized_clipped_h = standardized_h.clip(-3, 3)

# Get association between samples
sample_associations = ccal.analyze.compare_matrices(standardized_clipped_h, standardized_clipped_h, axis=1)

# Assign labels using each k
labels = pd.DataFrame(index=ks, columns=list(sample_associations.index) + ['cophenetic_correlation'])
labels.index.name = 'state'
labels.columns.name = 'samples'
for k in ks:
    print_log('Clustering with k = {} ...'.format(k))
    
    # For nclustering times, cluster sample associations and assign labels using this k
    nclustering_labels = pd.DataFrame(index=range(nclustering), columns=sample_associations.index)
    for i in range(nclustering):
        print_log('\tClustering #{} ...'.format(i))
        ward = AgglomerativeClustering(n_clusters=k)
        ward.fit(sample_associations)
        nclustering_labels.iloc[i, :] = ward.labels_

    # Count number of co-clustering (in the nclustering clusters) between samples
    ncoclusterings = pd.DataFrame(index=nclustering_labels.columns, columns=nclustering_labels.columns)
    ncoclusterings.fillna(0, inplace=True)
    for i, s in nclustering_labels.iterrows():
        print_log('\tCounting co-clustering at clustering #{} ...'.format(i))
        for i in s.index:
            for j in s.index:
                if i == j or s.ix[i] == s.ix[j]:
                    ncoclusterings.ix[i, j] += 1
    
    # Normalize by the nclustering and convert to distances
    distances = 1 - ncoclusterings / nclustering
    
    # Cluster the distances and assign the final label using this k
    ward = linkage(distances, method='ward')
    labels_ = fcluster(ward, k, criterion='maxclust')
    labels.ix[k, sample_associations.index] = labels_
    
    # Compute the cophenetic correlation, the correlation between cophenetic and Euclidian distances between samples
    labels.ix[k, 'cophenetic_correlation'] = cophenet(ward, pdist(distances))[0]

labels.to_csv(labels_filename, sep='\t')

# map_onco_gps

In [2]:
h = ccal.support.read_gct('../../../hematopoietic_cancer/result/ccle_hema/k9/ccle_hema_k_9_H.gct')

labels_filename = '~/Desktop/state_labels.txt'

states = 9
sample_stretch = 2
ngrids = 100

margin_factor = 1 / 24

figure_size = (10, 10)

delaunay_linewidth = 1
delaunay_linecolor = '#000000'

component_markersize = 15
component_markerfacecolor = '#0059b3'
component_markeredgewidth = delaunay_linewidth
component_markeredgecolor = '#ffffff'
component_text_verticalshift = 1
component_fontsize = 16

sample_markersize = 12
sample_markeredgewidth = 0.81
sample_markeredgecolor = '#000000'

contour_n = 15
contour_linewidth = 0.81
contour_linecolor = '#5a5a5a'
contour_alpha = 0.50

background_max_alpha = 1
background_markersize = 5.55

filename = '/Users/Kwat/Desktop/onco_gps'

In [3]:
# Standardize H and clip values less than -3 and more than 3
standardized_h = ccal.support.standardize_pandas_object(h)
standardized_clipped_h = standardized_h.clip(-3, 3)

# Project the H's components from <nsample>D to 2D, getting the x & y coordinates
# TODO: freeze random seed
mds = manifold.MDS()
components_coordinates = mds.fit_transform(standardized_clipped_h)

# Delaunay triangulate the components' 2D projected coordinates
delaunay = Delaunay(components_coordinates)

# Compute convexhull for the components' 2D projected coordinates
convexhull = ConvexHull(components_coordinates)
convexhull_region = mpl.path.Path(convexhull.points[convexhull.vertices])

# Sample and their state labels and x & y coordinates computed using Delaunay triangulation simplices
samples = pd.DataFrame(index=h.columns, columns=['state', 'x', 'y'])

# Get sample labels
labels = pd.read_csv(labels_filename, sep='\t', index_col=0)
samples.ix[:, 'state'] = labels.ix[states, :].astype(int)

# Get sample x & y coordinates using Delaunay triangulation simplices
for sample in samples.index:
    col = h.ix[:, sample]
    third = col.sort_values()[-3]
    col = col.mask(col < third, other=0)
    
    x = sum(col**sample_stretch * components_coordinates[:, 0]) / sum(col**sample_stretch)
    y = sum(col**sample_stretch * components_coordinates[:, 1]) / sum(col**sample_stretch)
    samples.ix[sample, ['x', 'y']] = x, y

In [4]:
# Set x & y coordinate boundaries
xcoordinates = np.concatenate((components_coordinates[:, 0], np.array(samples.ix[:, 'x'])))
xmin = min(xcoordinates)
xmax = max(xcoordinates)
xmargin = (xmax - xmin) * margin_factor
xmin -= xmargin
xmax += xmargin
ycoordinates = np.concatenate((components_coordinates[:, 1], np.array(samples.ix[:, 'y'])))
ymin = min(ycoordinates)
ymax = max(ycoordinates)
ymargin = (ymax - ymin) * margin_factor
ymin -= ymargin
ymax += ymargin

# Make x & y grids
xgrids = np.linspace(xmin, xmax, ngrids)
ygrids = np.linspace(ymin, ymax, ngrids)

# Get KDE for each state using bandwidth created from all states' x & y coordinates 
kdes = np.zeros((states + 1, ngrids, ngrids))
bandwidth_x = mass.bcv(np.array(samples.ix[:, 'x'].tolist()))[0]
bandwidth_y = mass.bcv(np.array(samples.ix[:, 'y'].tolist()))[0]
bandwidths = np.array([bandwidth_x, bandwidth_y]) / 2
for s in sorted(samples.ix[:, 'state'].unique()):
    coordiantes = samples.ix[samples.ix[:, 'state'] == s, ['x', 'y']]
    x = np.array(coordiantes.ix[:, 'x'], dtype=float)
    y = np.array(coordiantes.ix[:, 'y'], dtype=float)
    kde = mass.kde2d(x, y, bandwidths, n=np.array([ngrids]), lims=np.array([xmin, xmax, ymin, ymax]))
    kdes[s] = np.array(kde[2])

# Save x & y coordinates used for KDE (same for all states' KDEs)
xkde = np.array(kde[0])
ykde = np.array(kde[1])

# Assign the best KDE probability and state for each grid intersection
grid_probabilities = np.zeros((ngrids, ngrids))
grid_states = np.empty((ngrids, ngrids))
for i in range(ngrids):
    for j in range(ngrids):
        grid_probabilities[i, j] = max(kdes[:, j, i])
        grid_states[i, j] = np.argmax(kdes[:, i, j])

## plot

In [5]:
fig, ax = plt.subplots(figsize=figure_size)
ax.axis('off')

# Plot components
ax.plot(components_coordinates[:, 0], components_coordinates[:, 1], linestyle='', marker='D',
        markersize=component_markersize, markerfacecolor=component_markerfacecolor,
        markeredgewidth=component_markeredgewidth, markeredgecolor=component_markeredgecolor, zorder=6)

# Plot component name
for i in range(components_coordinates.shape[0]):
    ax.text(components_coordinates[i, 0], components_coordinates[i, 1] + component_text_verticalshift, standardized_clipped_h.index[i],
            fontsize=component_fontsize, weight='bold', color=component_markerfacecolor, horizontalalignment='center', zorder=6)

# Plot Delaunay triangulation
ax.triplot(delaunay.points[:, 0], delaunay.points[:, 1], delaunay.simplices.copy(),
           linewidth=delaunay_linewidth, color=delaunay_linecolor, zorder=4)

# Plot samples
for i, (idx, s) in enumerate(samples.iterrows()):
    ax.plot(s.ix['x'], s.ix['y'], marker='o', markersize=sample_markersize, markerfacecolor=CMAP_CATEGORICAL(int(s.ix['state'] / states * 255)),
            markeredgewidth=sample_markeredgewidth, markeredgecolor=sample_markeredgecolor, zorder=5)
    
# Plot sample legends
for i, state in enumerate(sorted(samples.ix[:, 'state'].unique())):
    ax.plot(xmax + 2, ymax - i, marker='o', markersize=sample_markersize, markerfacecolor=CMAP_CATEGORICAL(int(state / states * 255)),
            markeredgewidth=sample_markeredgewidth, markeredgecolor=sample_markeredgecolor, zorder=5)



# Plot contours
masked_coordinates = []
for i in range(ngrids):
    for j in range(ngrids):
        if not convexhull_region.contains_point((xkde[i], ykde[j])):
            masked_coordinates.append([i, j])
masked_coordinates = np.array(masked_coordinates)
z = grid_probabilities.copy()
z[masked_coordinates[:, 0], masked_coordinates[:, 1]] = np.nan
ax.contour(xkde, ykde, z, contour_n,
           linewidths=contour_linewidth, colors=contour_linecolor, alpha=contour_alpha, zorder=2)

ax.contour(xkde, ykde, grid_probabilities, contour_n,
           linewidths=contour_linewidth, colors=contour_linecolor, alpha=contour_alpha, zorder=2)

# Plot background
for i in range(ngrids):
    for j in range(ngrids):
        if convexhull_region.contains_point((xkde[i], ykde[j])):
             # Normalize color
            background_color = CMAP_CATEGORICAL(int(grid_states[i, j] / states * 255))

            # Background color is less saturated than the sample color
            background_alpha = min(background_max_alpha, (grid_probabilities[i, j] - grid_probabilities.min()) / (grid_probabilities.max() - grid_probabilities.min()))

            ax.plot(xkde[i], ykde[j], marker='s', markersize=background_markersize, markerfacecolor=background_color, alpha=background_alpha, zorder=1)
        #else:
            #ax.plot(xkde[i], ykde[j], marker='s', markersize=background_markersize * 1.1, markerfacecolor='w', zorder=3)

fig.savefig(filename)